## Crwal4AI (Crawl + Scrape)

In [1]:
!pip install crawl4ai

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 45.4/45.4 kB 1.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 431.3/431.3 kB 8.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 161.7/161.7 kB 13.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 10.3/10.3 MB 74.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 45.9/45.9 MB 16.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 45.9/45.9 MB 15.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 263.3/263.3 kB 18.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 57.3/57.3 kB 4.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 93.0/93.0 kB 8.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 4.5/4.5 MB 98.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 278.1/278.1 kB 17.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 507.6/507.6 kB 32.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 73

In [1]:
!crawl4ai-setup

[INIT].... → Running post-installation setup... 
[INIT].... → Installing Playwright browsers... 
Installing dependencies...
Get:1 https://cli.github.com/packages stable InRelease [3,917 B]
Get:2 https://cloud.r-project.org/bin/linux/ubuntu jammy-cran40/ InRelease [3,632 B]
Get:3 http://security.ubuntu.com/ubuntu jammy-security InRelease [129 kB]
Get:4 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu2204/x86_64  InRelease [1,581 B]
Hit:5 http://archive.ubuntu.com/ubuntu jammy InRelease
Get:6 https://cli.github.com/packages stable/main amd64 Packages [344 B]
Get:7 http://archive.ubuntu.com/ubuntu jammy-updates InRelease [128 kB]
Get:8 https://r2u.stat.illinois.edu/ubuntu jammy InRelease [6,555 B]
Get:9 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu2204/x86_64  Packages [2,102 kB]
Get:10 http://archive.ubuntu.com/ubuntu jammy-backports InRelease [127 kB]
Hit:11 https://ppa.launchpadcontent.net/deadsnakes/ppa/ubuntu jammy InRelease
Hit:12 https://ppa.launchp

In [2]:
!crawl4ai-doctor

[INIT].... → Running Crawl4AI health check... 
[INIT].... → Crawl4AI 0.7.6 
[TEST].... ℹ Testing crawling capabilities... 
[EXPORT].. ℹ Exporting media (PDF/MHTML/screenshot) took 3.15s 
[FETCH]... ↓ https://crawl4ai.com                                               
| ✓ | ⏱: 7.75s 
[SCRAPE].. ◆ https://crawl4ai.com                                               
| ✓ | ⏱: 0.12s 
[COMPLETE] ● https://crawl4ai.com                                               
| ✓ | ⏱: 7.88s 
[COMPLETE] ● ✅ Crawling test passed! 


In [10]:
!pip install nest_asyncio

In [11]:
import nest_asyncio
nest_asyncio.apply()

In [3]:
import os
import hashlib

# Ensure output directory
OUTDIR = "docs"
os.makedirs(OUTDIR, exist_ok=True)

def sanitize_filename(url: str) -> str:
    """Create a safe filename from a URL."""
    h = hashlib.md5(url.encode("utf‐8")).hexdigest()
    return f"{h}.md"

In [7]:
# cell 1: imports & setup
import asyncio
from typing import List

from crawl4ai import AsyncWebCrawler
from crawl4ai.async_configs import BrowserConfig, CrawlerRunConfig

async def _scrape_one(crawler: AsyncWebCrawler, url: str, config: CrawlerRunConfig):
    """Scrape a single URL and save to file."""
    result = await crawler.arun(url=url, config=config)
    if result.success:
        fname = sanitize_filename(url)
        path = os.path.join(OUTDIR, fname)
        # Use raw_markdown (or fit_markdown) if you prefer trimmed content
        md = result.markdown.raw_markdown
        with open(path, "w", encoding="utf-8") as f:
            f.write(f"# Source: {url}\n\n")
            f.write(md)
        print(f"✅ Saved {url} → {path}")
    else:
        print(f"❌ Failed {url} : {result.error_message}")

In [12]:
# cell 2: sequential function
def scrape_sequential(urls: List[str],
                      headless: bool = True,
                      verbose: bool = False):
    """Scrape the given list of URLs one after the other."""
    browser_cfg = BrowserConfig(headless=headless, verbose=verbose)
    run_cfg = CrawlerRunConfig()  # you can set filters/thresholds if preferred
    async def _run():
        async with AsyncWebCrawler(config=browser_cfg) as crawler:
            for url in urls:
                await _scrape_one(crawler, url, run_cfg)
    asyncio.run(_run())

# cell 3: parallel function
def scrape_parallel(urls: List[str],
                    headless: bool = True,
                    verbose: bool = False,
                    max_concurrent: int = 5):
    """Scrape the given list of URLs in parallel (up to max_concurrent at a time)."""
    browser_cfg = BrowserConfig(headless=headless, verbose=verbose)
    run_cfg = CrawlerRunConfig()
    async def _run():
        async with AsyncWebCrawler(config=browser_cfg) as crawler:
            # create tasks
            sem = asyncio.Semaphore(max_concurrent)
            async def sem_task(u):
                async with sem:
                    await _scrape_one(crawler, u, run_cfg)
            tasks = [asyncio.create_task(sem_task(url)) for url in urls]
            await asyncio.gather(*tasks)
    asyncio.run(_run())


In [4]:
import requests
from xml.etree import ElementTree

def get_docs_urls(sitemap_url):
    """
    Fetches all URLs from the Pydantic AI documentation.
    Uses the sitemap (https://ai.pydantic.dev/sitemap.xml) to get these URLs.

    Returns:
        List[str]: List of URLs
    """
    try:
        response = requests.get(sitemap_url)
        response.raise_for_status()

        # Parse the XML
        root = ElementTree.fromstring(response.content)

        # Extract all URLs from the sitemap
        # The namespace is usually defined in the root element
        namespace = {'ns': 'http://www.sitemaps.org/schemas/sitemap/0.9'}
        urls = [loc.text for loc in root.findall('.//ns:loc', namespace)]

        return urls
    except Exception as e:
        print(f"Error fetching sitemap: {e}")
        return []

In [5]:
get_docs_urls("https://www.ontb.bf/sitemap.xml")

['https://www.ontb.bf/',
 'https://www.ontb.bf/ontb',
 'https://www.ontb.bf/actualites',
 'https://www.ontb.bf/partenaires',
 'https://www.ontb.bf/agendas',
 'https://www.ontb.bf/burkina-faso',
 'https://www.ontb.bf/richesses',
 'https://www.ontb.bf/burkina-faso/geographie',
 'https://www.ontb.bf/burkina-faso/ethnies',
 'https://www.ontb.bf/visites/sites-touristiques',
 'https://www.ontb.bf/visites/parcs',
 'https://www.ontb.bf/visites/musees',
 'https://www.ontb.bf/evenements',
 'https://www.ontb.bf/pratiques/formalites',
 'https://www.ontb.bf/pratiques/precautions-de-sante',
 'https://www.ontb.bf/logements',
 'https://www.ontb.bf/restaurants',
 'https://www.ontb.bf/galerie',
 'https://www.ontb.bf/galeries-par-site',
 'https://www.ontb.bf/contact',
 'https://www.ontb.bf/visites/sites-touristiques/Laongo',
 'https://www.ontb.bf/visites/sites-touristiques/les-domes-de-fabedougou',
 'https://www.ontb.bf/visites/sites-touristiques/les-cascades-de-karfiguela-banfora',
 'https://www.ontb.bf

In [14]:
urls_to_scrape = get_docs_urls("https://www.ontb.bf/sitemap.xml")

scrape_sequential(urls_to_scrape, headless=True, verbose=True)

[INIT].... → Crawl4AI 0.7.6 

[FETCH]... ↓ https://www.ontb.bf/                                                                                 |
✓ | ⏱: 4.88s 

[SCRAPE].. ◆ https://www.ontb.bf/                                                                                 |
✓ | ⏱: 0.26s 

[COMPLETE] ● https://www.ontb.bf/                                                                                 |
✓ | ⏱: 5.16s 

✅ Saved https://www.ontb.bf/ → docs/af47e4830da1cf8641d15a0e7b1b3588.md


...

✅ Saved https://www.ontb.bf/carte → docs/1a7508394153d47c6c9ec9db698c16d2.md


[FETCH]... ↓ https://www.ontb.bf/richesses/faso-danfani                                                           |
✓ | ⏱: 1.20s 

[SCRAPE].. ◆ https://www.ontb.bf/richesses/faso-danfani                                                           |
✓ | ⏱: 0.05s 

[COMPLETE] ● https://www.ontb.bf/richesses/faso-danfani                                                           |
✓ | ⏱: 1.27s 

✅ Saved https://www.ontb.bf/richesses/faso-danfani → docs/7c8e41a4c4ff59d77e7acbafa91d8a12.md


In [20]:
len(urls_to_scrape)

28

In [18]:
bt_urls = get_docs_urls("https://www.burkinatourism.com/sitemap.xml")
print(len(bt_urls))

879


In [19]:
bt_urls[:10]

['http://www.burkinatourism.com/',
 'https://www.burkinatourism.com/-Actualites-.html',
 'https://www.burkinatourism.com/-A-la-une-.html',
 'https://www.burkinatourism.com/-Sites-touristiques-.html',
 'https://www.burkinatourism.com/-Region-Du-Centre-.html',
 'https://www.burkinatourism.com/-EVENEMENT-.html',
 'https://www.burkinatourism.com/-Histoire-.html',
 'https://www.burkinatourism.com/-Region-De-L-Ouest-.html',
 'https://www.burkinatourism.com/-Region-De-Sahel-Burkinabe-.html',
 'https://www.burkinatourism.com/-Guide-.html']

In [21]:
# urls_to_scrape = get_docs_urls("https://www.burkinatourism.com/sitemap.xml")
scrape_parallel(bt_urls, headless=True, verbose=True, max_concurrent=5)

[INIT].... → Crawl4AI 0.7.6 

[FETCH]... ↓ https://www.burkinatourism.com/-Region-Du-Centre-.html                                               |
✓ | ⏱: 11.40s 

[SCRAPE].. ◆ https://www.burkinatourism.com/-Region-Du-Centre-.html                                               |
✓ | ⏱: 0.53s 

[COMPLETE] ● https://www.burkinatourism.com/-Region-Du-Centre-.html                                               |
✓ | ⏱: 12.00s 

✅ Saved https://www.burkinatourism.com/-Region-Du-Centre-.html → docs/7c158b8d4d1851c65bbfe79056605332.md


...

✅ Saved https://www.burkinatourism.com/Fespaco-2013-101-films-de-35-pays-programmes-en-competition-officielle.html → docs/ec27beca614bbcc7c4fa439e6a7e4928.md


[FETCH]... ↓ https://www.burkinatourism.com/FESPACO-Les-pionniers-honores-a-Ouaga-Historique-DU-FESPACO.html      |
✓ | ⏱: 10.37s 

[SCRAPE].. ◆ https://www.burkinatourism.com/FESPACO-Les-pionniers-honores-a-Ouaga-Historique-DU-FESPACO.html      |
✓ | ⏱: 0.21s 

[COMPLETE] ● https://www.burkinatourism.com/FESPACO-Les-pionniers-honores-a-Ouaga-Historique-DU-FESPACO.html      |
✓ | ⏱: 10.60s 

✅ Saved https://www.burkinatourism.com/FESPACO-Les-pionniers-honores-a-Ouaga-Historique-DU-FESPACO.html → docs/ab6bfa8fc6cbd835ef47296eb0ce0d1d.md


In [22]:
!du -hd 1 docs/

14M	docs/


In [25]:
import os
import json


def map_urls_to_files(urls, output_dir="docs", json_path="url_map.json"):
    """
    Takes a list of URLs and creates/updates a JSON mapping file
    linking each URL to its sanitized Markdown file path.

    Args:
        urls (list[str]): List of URLs.
        output_dir (str): Directory where markdown files are (or will be) saved.
        json_path (str): Path to the JSON mapping file.
    """
    os.makedirs(output_dir, exist_ok=True)

    # Load existing mapping if available
    if os.path.exists(json_path):
        try:
            with open(json_path, "r", encoding="utf-8") as f:
                url_map = json.load(f)
        except (json.JSONDecodeError, FileNotFoundError):
            url_map = {}
    else:
        url_map = {}

    # Add or update mappings
    for url in urls:
        file_name = sanitize_filename(url)
        file_path = os.path.join(output_dir, file_name)
        url_map[file_name[:-3]] = {"source": url, "file_path": file_path}

    # Save updated mapping
    with open(json_path, "w", encoding="utf-8") as f:
        json.dump(url_map, f, indent=2, ensure_ascii=False)

    print(len(urls), "added successfully.")


In [26]:
map_urls_to_files(urls_to_scrape)
map_urls_to_files(bt_urls)

28 added successfully.
879 added successfully.


## Qdrant Vectore DB

In [29]:
!pip install qdrant-client

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 337.3/337.3 kB 5.5 MB/s eta 0:00:00


In [ ]:
from sentence_transformers import SentenceTransformer

# Init embeddings model
embedding_model = SentenceTransformer("sentence-transformers/paraphrase-multilingual-MiniLM-L12-v2")

modules.json:   0%|          | 0.00/229 [00:00<?, ?B/s]

config_sentence_transformers.json:   0%|          | 0.00/122 [00:00<?, ?B/s]

README.md: 0.00B [00:00, ?B/s]

sentence_bert_config.json:   0%|          | 0.00/53.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/645 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/471M [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/480 [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/9.08M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/239 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/190 [00:00<?, ?B/s]

In [33]:
def read_markdown_file(path: str) -> str:
    """Read markdown file and return plain text content (no markdown removal performed)."""
    with open(path, "r", encoding="utf-8") as f:
        content = f.read()
    return content

In [34]:
def chunk_text_simple(text: str,
                      chunk_size_words: int = 150,
                      overlap_words: int = 30) -> List[str]:
    """
    Simple word-based sliding window chunker.
    Returns list of text chunks.
    """
    words = text.split()
    if len(words) == 0:
        return []
    chunks = []
    start = 0
    while start < len(words):
        end = start + chunk_size_words
        chunk_words = words[start:end]
        chunks.append(" ".join(chunk_words))
        if end >= len(words):
            break
        start = end - overlap_words  # overlap
    return chunks


In [ ]:
# from google.colab import userdata
# QDRANT_KEY = userdata.get('QDRANT_KEY')
# QDRANT_URL = userdata.get('QDRANT_URL')

In [ ]:
from qdrant_client import QdrantClient
from qdrant_client.models import PointStruct, VectorParams, Distance

qdrant_client = QdrantClient(
    url=QDRANT_URL,
    api_key=QDRANT_KEY,
)

VECTOR_SIZE = 384
COLLECTION_NAME = "bf_tourism"

def init_db():
    """Créer ou réinitialiser la collection Qdrant."""
    qdrant_client.recreate_collection(
        collection_name=COLLECTION_NAME,
        vectors_config=VectorParams(size=VECTOR_SIZE, distance=Distance.COSINE),
    )

init_db()
print(qdrant_client.get_collections())

/tmp/ipython-input-2629256104.py:14: DeprecationWarning: `recreate_collection` method is deprecated and will be removed in the future. Use `collection_exists` to check collection existence and `create_collection` instead.
  qdrant_client.recreate_collection(


collections=[CollectionDescription(name='bf_tourism')]


In [35]:
with open("url_map.json", "r", encoding="utf-8") as f:
    url_map = json.load(f)

In [76]:
from tqdm.auto import tqdm
import uuid

points = []
for file_id in tqdm(url_map):
    src_url, path = tuple(url_map[file_id].values())

    content = read_markdown_file(path)
    chunks = chunk_text_simple(content)
    for id, chunk in enumerate(chunks):
        vector = embedding_model.encode(chunk).tolist()
        points.append(PointStruct(id=uuid.uuid4().hex, vector=vector, payload={"source": src_url, "text": chunk}))


  0%|          | 0/907 [00:00<?, ?it/s]

In [ ]:
# Send points using batch to avoid large uploads
BATCH_SIZE = 32
for i in tqdm(range(len(points)//BATCH_SIZE)):
    qdrant_client.upsert(collection_name=COLLECTION_NAME, points=points[i*BATCH_SIZE:(i+1)*BATCH_SIZE])


  0%|          | 0/214 [00:00<?, ?it/s]